In [1]:
pip install underthesea

Note: you may need to restart the kernel to use updated packages.


In [2]:
pip install openpyxl

Note: you may need to restart the kernel to use updated packages.


In [3]:
pip install openai

Note: you may need to restart the kernel to use updated packages.


In [4]:
import pandas as pd
import openai
import time
from tqdm.auto import tqdm
from underthesea import sent_tokenize
import json
import re

In [ ]:
# Cài đặt OpenAI Client
client = openai.OpenAI(
    api_key="",  # Thay API key
)

In [6]:
def convert_sentence(text):
    sentences = sent_tokenize(text)
    return sentences

def getSize_content(content):
    size = len(content)
    return size

def getSize_sentence(sentence):
    size = len(sentence.split(" "))
    return size

def add_messages(message, prompt):
    return message + [{'role': 'user', 'content': prompt}]

def get_prompt(title, context):
    return """Chủ đề: {}
    Đoạn văn: {}
    """.format(title,
               context.strip()
              ).strip()

def ask(messages, title, context):
    prompt = get_prompt(title, context)
    new_messages = add_messages(messages, prompt)
    answer = client.chat.completions.create(
      model="gpt-4o",
    #   model="gpt-3.5-turbo",
      messages=new_messages,
      temperature=0
    )
    return answer

def get_time(start_time, end_time):
    cost = round(end_time - start_time)
    return "{}:{}".format(cost // 60, cost % 60)

In [7]:
def test_sentiment_score(init_messages, content):
    content_processed = convert_sentence(content)
    title = 'Tin tức'
    text = ' '.join(content_processed)
    response = ask(init_messages, title, text)
    # Trích xuất nội dung từ response

    result = response.choices[0].message.content
    print("result " + str(result))

In [8]:
init_user_prompt = """Chủ đề: Tin tức
Đoạn văn: Mục tiêu đón 8 triệu lượt khách quốc tế trong năm nay sẽ khó khả thi nếu chúng ta không có những động thái quyết liệt để xóa bỏ những rào cản với du khách, trong đó đầu tiên là chính sách visa. Kết thúc năm 2022, Việt Nam đang đứng cuối bảng phục hồi du lịch quốc tế của khu vực với tỷ lệ phục hồi chỉ 18,1%. Trong khi đó, tỷ lệ này ở các nước láng giềng như Thái Lan, Singapore, Malaysia hay Campuchia đều đạt từ 26 đến 31%. Với thực tế này, nếu không có giải pháp đột phá, tháo gỡ những rào cản hiện hữu, thì mục tiêu đón 8 triệu lượt du khách quốc tế năm 2023 của nước ta khó lòng đạt được. Đồng nghĩa, du lịch Việt Nam sẽ vuột cơ hội hút nguồn doanh thu lớn từ “mỏ vàng” khách quốc tế để nhanh chóng phục hồi.Theo giới chuyên môn, một trong những rào cản lớn đầu tiên khiến du khách quốc tế không mặn mà đến Việt Nam là hạn chế trong chính sách visa.Những bất cập trong chính sách visaAnh Yan Nang Oo, du khách Myanmar, cùng bạn đi du lịch Việt Nam. Do chỉ được cấp visa 14 ngày trong khi nhóm bạn muốn khám phá nhiều điểm đến tại Việt Nam nên họ phải lên kế hoạch di chuyển gấp từ Hạ Long, Hà Nội, Huế, Đà Nẵng, Phú Quốc. “Hôm ra sân bay để check-out về nước vừa hết 14 ngày, cũng may thủ tục xuất cảnh thuận lợi, không gặp vấn đề gì”, du khách này thở phào.Nhiều khách quốc tế mong muốn chính sách visa của Việt Nam được nới lỏng, cho phép du khách kéo dài thời hạn để có nhiều thời gian khám phá và trải nghiệm. Đó cũng là mong muốn của rất nhiều du khách quốc tế. Theo thống kê, Việt Nam chỉ miễn thị thực cho công dân của 24 quốc gia. Ðây là con số quá ít ỏi khi so sánh với các nước láng giềng như Singapore miễn visa cho 162 nước, Philippines là 157 nước, Malaysia là 162 nước, Thái Lan là 64 nước"""
init_system_prompt = f'''Bạn là trợ lý hữu ích giúp tạo các cặp 'khía cạnh' - 'cảm xúc' từ một 'đoạn bài báo thời sự' cho cổ phiếu ACB. Dưới đây là các yêu cầu khi trích xuất khía cạnh và cảm xúc:
1. Các khía cạnh được trích xuất bao gồm: Reputation (Danh tiếng của công ty); Company Communication (Truyền thông của công ty); Appointment (Bổ nhiệm); Financial (Tài chính); Regulatory (Cơ quan quản lí, chính sách); Sales (Bán hàng); M&A (Merge & Acquisition): Sáp nhập; Legal (Luật, tính hợp pháp); Dividend Policy (Chính sách cổ tức); Risks (rủi ro - ví dụ operation risk, credit risk - rủi ro tín dụng, reputation risk); Rumors (tin đồn); Strategy (chiến lược); Options (quyền chọn); IPO (initial public offering): lên sàn, niêm yết; Signal (tín hiệu để mua bán cổ phiếu); Coverage (báo cáo khuyến nghị buy sell hold của analysts); Fundamentals (các chỉ số trong phân tích cơ bản như P/E, P/B, Liabilites to Asset ratio); Insider Activity (các hoạt động nội bộ của công ty); Price Action (biến động giá); Buyside (các quĩ đầu tư, công ty nhỏ) ngược với sellside IB (Investment Banks); Technical Analysis (Phân tích kĩ thuật); Trade (thương mại, xuất nhập khẩu); Central Banks (Ngân hàng Trung ương, ở VN: Ngân hàng nhà nước, SBV); Currency (tiền tệ, tỉ giá); Conditions (điều kiện); Market (thị trường); Volatility (độ biến động, rủi ro); Investor Sentiment (Tâm lý chung của nhà đầu tư) lạc quan, lo lắng, chờ đợi...; Retail Investor Behavior (Hành vi của nhà đầu tư cá nhân) FOMO, hoảng loạn, giữ tiền mặt…; Speculation (Đầu cơ, hành vi đầu tư theo tin đồn hoặc kỳ vọng ngắn hạn); Domestic Institutional Behavior (Hành vi của tổ chức trong nước: tự doanh, bảo hiểm, quỹ trong nước) mua ròng, bán ròng, giảm tỷ trọng, rút khỏi cổ phiếu, các giao dịch thỏa thuận lớn giữa các tổ chức nội bộ; Foreign Institutional Behavior (Hành vi của nhà đầu tư tổ chức nước ngoài: ETF, quỹ ngoại, nhà đầu tư nước ngoài) mua ròng, bán ròng, tin tức đưa cổ phiếu vào, ra danh mục ETF, cảnh báo rủi ro, hạ mức xếp hạng cổ phiếu từ các tổ chức nước ngoài; Black Swan Event (Sự kiện thiên nga đen: hiếm gặp, khó dự đoán, gây ảnh hưởng nghiêm trọng như khủng hoảng, chiến tranh, dịch bệnh...).
2. Ảnh hưởng nội dung đến các khía cạnh tương ứng. Với mỗi chỉ số ảnh hưởng nên là số thực trong khoảng từ -1 (thật sự tiêu cực) đến 1 (thật sự tích cực)
3. Đảm bảo rằng các khía cạnh mà bạn trích xuất liên quan đến vấn đề của đoạn bài báo thời sự. Và khía cạnh nào bạn phân vân hãy xem không ảnh hưởng thì đánh là 0.
4. Chú ý là dựa vào ảnh hưởng của nội dung đến các khía cạnh. Khi cho tôi kết quả hãy theo format: có kí tự '#' trước khía cạnh, phía sau khía cạnh là con số ảnh hưởng nội dung, ví dụ về format '#khía cạnh1 1#khía cạnh2 -1#khía cạnh3 0'. Tuân thủ theo format của tôi, không làm khác.'''
init_assistant = """#Reputation 0.0#Company Communication 0.0#Appointment 0.0#Financial -0.3#Regulatory -0.4#Sales -0.3#M&A 0.0#Legal -0.1#Dividend Policy 0.0#Risks -0.5#Rumors 0.0#Strategy -0.4#Options 0.0#IPO 0.0#Signal -0.2#Coverage 0.0#Fundamentals -0.2#Insider Activity 0.0#Price Action 0.0#Buyside 0.0#Technical Analysis 0.0#Trade -0.1#Central Banks 0.0#Currency 0.0#Conditions -0.5#Market -0.3#Volatility -0.4#Investor Sentiment -0.6#Retail Investor Behavior -0.4#Speculation 0.0#Domestic Institutional Behavior -0.2#Foreign Institutional Behavior -0.3#Black Swan Event 0.0"""

init_messages = [
    {"role": "system", "content": init_system_prompt},
    {"role": "user", "content": init_user_prompt},
    {"role": "assistant", "content": init_assistant},
]

In [33]:
content = '''Thông tin nêu tại báo cáo tài chính công bố sáng 24/10. Trong đó, mức tăng trưởng tín dụng cao gấp 1,5 lần so với bình quân ngành. Huy động tính đến ngày 30/9 đạt 512.000 tỷ đồng, tăng 6,1% so với đầu năm. Ngân hàng tiếp tục giữ ưu thế trong mảng bán lẻ và thực hiện chiến lược tăng trưởng cân bằng giữa cá nhân và doanh nghiệp. Ghi nhận lũy kế tín dụng mảng doanh nghiệp trong 9 tháng qua có tốc độ hơn 15%.
Về tiền gửi không kỳ hạn (Current Account Savings Account - CASA), ACB đẩy mạnh các giải pháp thu hút thông qua gia tăng tiện ích cho khách hàng. Tiêu biểu như chiến dịch "Đồng minh thông thái" cung cấp giải pháp, tiện ích quản lý cửa hàng cho các hộ kinh doanh. Đơn vị còn nâng cấp các dịch vụ tài chính cao cấp dành cho nhóm khách hàng ưu tiên. Nhờ đó, huy động không kỳ hạn đạt 114.000 tỷ đồng, tăng 24% so với cùng kỳ năm 2023, tiếp tục là một trong những ngân hàng bán lẻ có tỷ lệ CASA cao nhất thị trường ở mức 22,2%.
Bên ngoài trụ sở ngân hàng tại Hà Nội. Ảnh: ACB
Báo cáo tài chính cũng nêu mức lợi nhuận trước thuế của ngân hàng này trong 9 tháng đầu năm là 15.300 tỷ đồng, tăng 2% so với cùng kỳ, chủ yếu từ tăng trưởng quy mô tín dụng, phí dịch vụ và quản lý chi phí hiệu quả. Giai đoạn 2019-2023, ACB là một trong những ngân hàng có tốc độ tăng trưởng kép cao nhất ngành (khoảng 28% mỗi năm) và duy trì tăng trưởng cao ngay cả trong bối cảnh nền kinh tế nhiều khó khăn.
Tỷ lệ nợ xấu quý III/2024 của ACB ở mức 1,49%, thuộc nhóm những ngân hàng có nợ xấu thấp nhất thị trường. Chi phí trích lập dự phòng thấp hơn mức trích bình quân trong hai quý đầu năm.
Các quy định về tỷ lệ an toàn thanh khoản theo quy định của Ngân hàng Nhà nước được ACB tuân thủ nghiêm ngặt với tỷ lệ cho vay trên tổng tiền gửi (LDR) là 82,4%, tỷ lệ vốn ngắn hạn cho vay trung và dài hạn chiếm 20,7%. Tỷ lệ an toàn vốn (riêng lẻ) tới cuối quý III ở mức 11,3%, vượt xa so với mức quy định của Ngân hàng Nhà nước. Bên cạnh đó, ACB đã tối ưu chi phí hoạt động ở mức 8.200 tỷ đồng, tăng nhẹ 3,8% so với cùng kỳ. Tỷ lệ CIR được duy trì ở mức thấp 32,7%. ROE vẫn duy trì ở mức 22,2%, tiếp tục nằm trong nhóm dẫn đầu ngành.
Công ty chứng khoán ACB - ACBS cũng tiếp tục ghi nhận kết quả kinh doanh tốt trong quý III với lợi nhuận trước thuế tăng trưởng hơn 44% so với cùng kỳ. Lũy kế 9 tháng đầu năm, lợi nhuận trước thuế của ACBS tăng 67% nhờ tăng trưởng thu nhập từ các hoạt động kinh doanh chính, gồm thu nhập lãi cho vay margin, hoạt động tự doanh và hoạt động môi giới. Công ty đạt thị phần 2,68%, tăng 0,24%.
Bên cạnh các chỉ số tăng trưởng, ACB tiếp tục đạt nhiều thành tựu về ngân hàng số và phát triển bền vững.
Theo định hướng của Chính phủ về tăng trưởng xanh 2021-2030, nhà băng triển khai các hoạt động kinh doanh phù hợp với chương trình hành động phát triển bền vững của ngành ngân hàng. Điều này góp phần không nhỏ vào kết quả kinh doanh tích cực 9 tháng đầu năm.
Các sản phẩm, dịch vụ Ngân hàng số ACB One được đẩy mạnh. Tính đến cuối quý III, doanh số giao dịch và số lượng giao dịch online tăng lần lượt tăng 32% và 57% so với năm 2023. ACB One được khách hàng đánh giá cao với trải nghiệm tiện lợi, chương trình tích điểm giao dịch đổi quà phong phú, phù hợp với nhu cầu đa dạng.
ACB cũng nâng hạn mức gói tín dụng xanh, xã hội từ 2.000 tỷ đồng lên 4.000 tỷ đồng với mức lãi suất chỉ từ 6% một năm, ưu đãi lên đến 24 tháng. Tính đến hết tháng 9, đơn vị giải ngân 2.900 tỷ đồng trong gói tín dụng này.
Trước đó, nhà băng đã công bố Khung Tài chính bền vững, tạo nên các tiêu chuẩn cho hoạt động trong lĩnh vực tài chính xanh. Trong sự kiện "Khơi thông vốn, đón cơ hội" kết nối giữa ngân hàng và doanh nghiệp mới đây, ông Từ Tiến Phát,Tổng giám đốc ACB, cho biết, ngân hàng hiện dành khoảng 5.000 tỷ đồng tài trợ vốn cho các doanh nghiệp vừa và nhỏ, đáp ứng phục vụ nhu cầu sản xuất, kinh doanh, xuất nhập khẩu. Gói tín dụng này có thể tăng lên 10.000 tỷ đồng hoặc 20.000 tỷ đồng nếu doanh nghiệp có nhu cầu về vốn tín dụng xanh để đáp ứng yêu cầu của đối tác nước ngoài.
Trong phiên giao dịch, cổ phiếu ACB được khối ngoại mua rồng 200000 tỷ, trong khi đó ACB bị tự doanh và các tổ chức trong nước lại bán rồng 100000 tỷ
Trái ngược với ACB, VCB có kết quả tệ hại về mọi mặc đặt ra mối lo ngại lớn cho doanh nghiệp
Hoàng Anh'''

In [31]:
#ticker vcb
test_sentiment_score(init_messages, content)

result #Reputation -0.5#Company Communication 0.0#Appointment 0.0#Financial -0.6#Regulatory 0.0#Sales 0.0#M&A 0.0#Legal 0.0#Dividend Policy 0.0#Risks -0.5#Rumors 0.0#Strategy -0.4#Options 0.0#IPO 0.0#Signal -0.5#Coverage 0.0#Fundamentals -0.6#Insider Activity 0.0#Price Action -0.4#Buyside 0.0#Technical Analysis 0.0#Trade 0.0#Central Banks 0.0#Currency 0.0#Conditions -0.5#Market -0.4#Volatility -0.5#Investor Sentiment -0.6#Retail Investor Behavior -0.5#Speculation 0.0#Domestic Institutional Behavior -0.4#Foreign Institutional Behavior -0.3#Black Swan Event 0.0


In [34]:
#ticker acb
test_sentiment_score(init_messages, content)

result #Reputation 0.5#Company Communication 0.3#Appointment 0.0#Financial 0.7#Regulatory 0.2#Sales 0.4#M&A 0.0#Legal 0.0#Dividend Policy 0.0#Risks 0.1#Rumors 0.0#Strategy 0.5#Options 0.0#IPO 0.0#Signal 0.4#Coverage 0.0#Fundamentals 0.6#Insider Activity 0.0#Price Action 0.3#Buyside 0.0#Technical Analysis 0.0#Trade 0.3#Central Banks 0.0#Currency 0.0#Conditions 0.2#Market 0.4#Volatility 0.1#Investor Sentiment 0.5#Retail Investor Behavior 0.0#Speculation 0.0#Domestic Institutional Behavior -0.3#Foreign Institutional Behavior 0.4#Black Swan Event 0.0


In [28]:
#ticker vhm
test_sentiment_score(init_messages, content)

result #Reputation 0.0#Company Communication 0.0#Appointment 0.0#Financial 0.0#Regulatory 0.0#Sales 0.0#M&A 0.0#Legal 0.0#Dividend Policy 0.0#Risks 0.0#Rumors 0.0#Strategy 0.0#Options 0.0#IPO 0.0#Signal 0.0#Coverage 0.0#Fundamentals 0.0#Insider Activity 0.0#Price Action 0.0#Buyside 0.0#Technical Analysis 0.0#Trade 0.0#Central Banks 0.0#Currency 0.0#Conditions 0.0#Market 0.0#Volatility 0.0#Investor Sentiment 0.0#Retail Investor Behavior 0.0#Speculation 0.0#Domestic Institutional Behavior 0.0#Foreign Institutional Behavior 0.0#Black Swan Event 0.0


In [ ]:
# ==========================tubo-3.5=========================================

In [21]:
#ticker vcb
test_sentiment_score(init_messages, content)

result #Reputation 0.0#Company Communication 0.0#Appointment 0.0#Financial 0.8#Regulatory 0.6#Sales 0.0#M&A 0.0#Legal 0.0#Dividend Policy 0.0#Risks 0.7#Rumors 0.0#Strategy 0.8#Options 0.0#IPO 0.0#Signal 0.6#Coverage 0.0#Fundamentals 0.8#Insider Activity 0.0#Price Action 0.0#Buyside 0.0#Technical Analysis 0.0#Trade 0.0#Central Banks 0.0#Currency 0.0#Conditions 0.7#Market 0.0#Volatility 0.0


In [17]:
# ticker acb
test_sentiment_score(init_messages, content)

result #Reputation 0.2#Company Communication 0.3#Appointment 0.0#Financial 0.8#Regulatory 0.5#Sales 0.4#M&A 0.0#Legal 0.0#Dividend Policy 0.0#Risks 0.6#Rumors 0.0#Strategy 0.7#Options 0.0#IPO 0.0#Signal 0.6#Coverage 0.0#Fundamentals 0.8#Insider Activity 0.0#Price Action 0.0#Buyside 0.0#Technical Analysis 0.0#Trade 0.0#Central Banks 0.0#Currency 0.0#Conditions 0.7#Market 0.5#Volatility 0.4


In [19]:
#ticker vhm
test_sentiment_score(init_messages, content)

result #Reputation 0.0#Company Communication 0.0#Appointment 0.0#Financial 0.8#Regulatory 0.6#Sales 0.0#M&A 0.0#Legal 0.0#Dividend Policy 0.0#Risks 0.7#Rumors 0.0#Strategy 0.8#Options 0.0#IPO 0.0#Signal 0.6#Coverage 0.0#Fundamentals 0.8#Insider Activity 0.0#Price Action 0.0#Buyside 0.0#Technical Analysis 0.0#Trade 0.0#Central Banks 0.0#Currency 0.0#Conditions 0.0#Market 0.0#Volatility 0.0


In [ ]:
# ===================================gpt 4o======================================

In [35]:
# ticker acb
test_sentiment_score(init_messages, content)

result #Reputation 0.8#Company Communication 0.7#Appointment 0.0#Financial 0.9#Regulatory 0.5#Sales 0.6#M&A 0.0#Legal 0.0#Dividend Policy 0.0#Risks 0.3#Rumors 0.0#Strategy 0.8#Options 0.0#IPO 0.0#Signal 0.7#Coverage 0.0#Fundamentals 0.9#Insider Activity 0.0#Price Action 0.0#Buyside 0.0#Technical Analysis 0.0#Trade 0.5#Central Banks 0.0#Currency 0.0#Conditions 0.0#Market 0.6#Volatility 0.0


In [ ]:
#ticker vhm
test_sentiment_score(init_messages, content)

result #Reputation 0.0#Company Communication 0.0#Appointment 0.0#Financial 0.0#Regulatory 0.0#Sales 0.0#M&A 0.0#Legal 0.0#Dividend Policy 0.0#Risks 0.0#Rumors 0.0#Strategy 0.0#Options 0.0#IPO 0.0#Signal 0.0#Coverage 0.0#Fundamentals 0.0#Insider Activity 0.0#Price Action 0.0#Buyside 0.0#Technical Analysis 0.0#Trade 0.0#Central Banks 0.0#Currency 0.0#Conditions 0.0#Market 0.0#Volatility 0.0


In [ ]:
#ticker vcb
test_sentiment_score(init_messages, content)

result #Reputation -0.5#Company Communication 0.0#Appointment 0.0#Financial -0.7#Regulatory 0.0#Sales 0.0#M&A 0.0#Legal 0.0#Dividend Policy 0.0#Risks -0.6#Rumors 0.0#Strategy -0.5#Options 0.0#IPO 0.0#Signal -0.6#Coverage 0.0#Fundamentals -0.7#Insider Activity 0.0#Price Action -0.5#Buyside 0.0#Technical Analysis 0.0#Trade 0.0#Central Banks 0.0#Currency 0.0#Conditions -0.6#Market -0.5#Volatility -0.5


In [ ]:
#ticker acb
test_sentiment_score(init_messages, content)

result #Reputation 0.8#Company Communication 0.7#Appointment 0.0#Financial 0.9#Regulatory 0.5#Sales 0.6#M&A 0.0#Legal 0.0#Dividend Policy 0.0#Risks 0.2#Rumors 0.0#Strategy 0.8#Options 0.0#IPO 0.0#Signal 0.7#Coverage 0.0#Fundamentals 0.9#Insider Activity 0.0#Price Action 0.0#Buyside 0.0#Technical Analysis 0.0#Trade 0.5#Central Banks 0.0#Currency 0.0#Conditions 0.0#Market 0.6#Volatility 0.0


In [ ]:
# ============================================================sentiment score for stock========================

In [8]:
def parse_sentiment_result(sentiment_str):
    """
    Phân tích chuỗi như '#Reputation 0.2#Financial -0.3...' thành dict
    """
    pattern = r"#([\w\s&\-]+)\s(-?\d+\.?\d*)"
    return {match[0].strip(): float(match[1]) for match in re.findall(pattern, sentiment_str)}

In [38]:
print(parse_sentiment_result(init_assistant))

{'Reputation': 0.0, 'Company Communication': 0.0, 'Appointment': 0.0, 'Financial': -0.3, 'Regulatory': -0.4, 'Sales': -0.3, 'M&A': 0.0, 'Legal': -0.1, 'Dividend Policy': 0.0, 'Risks': -0.5, 'Rumors': 0.0, 'Strategy': -0.4, 'Options': 0.0, 'IPO': 0.0, 'Signal': -0.2, 'Coverage': 0.0, 'Fundamentals': -0.2, 'Insider Activity': 0.0, 'Price Action': 0.0, 'Buyside': 0.0, 'Technical Analysis': 0.0, 'Trade': -0.1, 'Central Banks': 0.0, 'Currency': 0.0, 'Conditions': -0.5, 'Market': -0.3, 'Volatility': -0.4, 'Investor Sentiment': -0.6, 'Retail Investor Behavior': -0.4, 'Speculation': 0.0, 'Domestic Institutional Behavior': -0.2, 'Foreign Institutional Behavior': -0.3, 'Black Swan Event': 0.0}


In [9]:
def score_sentiment(original_file, destination_file, init_messages):

  df = pd.read_excel(original_file)
  # Xóa các dòng không có nội dung ở cột 'Content'
  df = df[df['Content'].notnull() & (df['Content'].str.strip() != '')]
  tqdm.pandas(desc="Đang phân tích cảm xúc")

  sentiments = []

  for i, (_, row) in enumerate(tqdm(df.iterrows(), total=len(df), desc="Phân tích tin tức"), start=1):
    paper_title_processing = row.get('tittle', f"Không có tiêu đề")
    content = row['Content']
    if not isinstance(content, str):
        content = str(content)
    content_processed = convert_sentence(content)
    title = 'Tin tức'
    text = ' '.join(content_processed)
    # In chỉ tiêu đề bài báo
    print(f"\n📝 Đang chấm điểm xúc cảm cho bài báo thứ {i}/{len(df)}: Tiêu đề: {paper_title_processing}")

    try:

      response = ask(init_messages, title, text)
      print("response " + str(response))

      # Trích xuất nội dung từ response

      result = response.choices[0].message.content
      print("result " + str(result))
      # sentiment_data = json.loads(result)
      sentiment_data = parse_sentiment_result(result)
      print("sentiment_data " + str(sentiment_data))

    except Exception as e:

      sentiment_data = {"error": str(e)}
    sentiments.append(sentiment_data)

    # Tránh rate limit
    time.sleep(4)

    # Gộp các cảm xúc vào các cột mới trong df
  sentiment_df = pd.DataFrame(sentiments)
  df = pd.concat([df.reset_index(drop=True), sentiment_df.reset_index(drop=True)], axis=1)

  # Lưu ra file đích
  with pd.ExcelWriter(destination_file, engine='openpyxl', mode='w') as writer:
    df.to_excel(writer, sheet_name='Sheet1', index=False)
  print("Đã lưu " +str(destination_file))



In [10]:
init_user_prompt = """Chủ đề: Tin tức
Đoạn văn: Mục tiêu đón 8 triệu lượt khách quốc tế trong năm nay sẽ khó khả thi nếu chúng ta không có những động thái quyết liệt để xóa bỏ những rào cản với du khách, trong đó đầu tiên là chính sách visa. Kết thúc năm 2022, Việt Nam đang đứng cuối bảng phục hồi du lịch quốc tế của khu vực với tỷ lệ phục hồi chỉ 18,1%. Trong khi đó, tỷ lệ này ở các nước láng giềng như Thái Lan, Singapore, Malaysia hay Campuchia đều đạt từ 26 đến 31%. Với thực tế này, nếu không có giải pháp đột phá, tháo gỡ những rào cản hiện hữu, thì mục tiêu đón 8 triệu lượt du khách quốc tế năm 2023 của nước ta khó lòng đạt được. Đồng nghĩa, du lịch Việt Nam sẽ vuột cơ hội hút nguồn doanh thu lớn từ “mỏ vàng” khách quốc tế để nhanh chóng phục hồi.Theo giới chuyên môn, một trong những rào cản lớn đầu tiên khiến du khách quốc tế không mặn mà đến Việt Nam là hạn chế trong chính sách visa.Những bất cập trong chính sách visaAnh Yan Nang Oo, du khách Myanmar, cùng bạn đi du lịch Việt Nam. Do chỉ được cấp visa 14 ngày trong khi nhóm bạn muốn khám phá nhiều điểm đến tại Việt Nam nên họ phải lên kế hoạch di chuyển gấp từ Hạ Long, Hà Nội, Huế, Đà Nẵng, Phú Quốc. “Hôm ra sân bay để check-out về nước vừa hết 14 ngày, cũng may thủ tục xuất cảnh thuận lợi, không gặp vấn đề gì”, du khách này thở phào.Nhiều khách quốc tế mong muốn chính sách visa của Việt Nam được nới lỏng, cho phép du khách kéo dài thời hạn để có nhiều thời gian khám phá và trải nghiệm. Đó cũng là mong muốn của rất nhiều du khách quốc tế. Theo thống kê, Việt Nam chỉ miễn thị thực cho công dân của 24 quốc gia. Ðây là con số quá ít ỏi khi so sánh với các nước láng giềng như Singapore miễn visa cho 162 nước, Philippines là 157 nước, Malaysia là 162 nước, Thái Lan là 64 nước"""
init_assistant = """#Reputation 0.0#Company Communication 0.0#Appointment 0.0#Financial -0.3#Regulatory -0.4#Sales -0.3#M&A 0.0#Legal -0.1#Dividend Policy 0.0#Risks -0.5#Rumors 0.0#Strategy -0.4#Options 0.0#IPO 0.0#Signal -0.2#Coverage 0.0#Fundamentals -0.2#Insider Activity 0.0#Price Action 0.0#Buyside 0.0#Technical Analysis 0.0#Trade -0.1#Central Banks 0.0#Currency 0.0#Conditions -0.5#Market -0.3#Volatility -0.4#Investor Sentiment -0.6#Retail Investor Behavior -0.4#Speculation 0.0#Domestic Institutional Behavior -0.2#Foreign Institutional Behavior -0.3#Black Swan Event 0.0"""

In [11]:
def score_sentiment_for_vn30(tickers):
  for ticker in tickers:
    print("Đang xử lý cho cổ phiếu "+str(ticker))
    original_file = rf'D:\thacsi\TAILIEULUANVAN\code\PredictStock_TA_FA_SA\SA\data\v2\news_vnexpress_vietnamnet_tuoitre\data_customize\{ticker}.xlsx'
    destination_file = rf'D:\thacsi\TAILIEULUANVAN\code\PredictStock_TA_FA_SA\SA\data\v2\sentiment_score_data\vnexpress_vietnamnet_tuoitre\v2\data\{ticker}.xlsx'

    init_system_prompt = f'''Bạn là trợ lý hữu ích giúp tạo các cặp 'khía cạnh' - 'cảm xúc' từ một 'đoạn bài báo thời sự' cho cổ phiếu {ticker}. Dưới đây là các yêu cầu khi trích xuất khía cạnh và cảm xúc:
1. Các khía cạnh được trích xuất bao gồm: Reputation (Danh tiếng của công ty); Company Communication (Truyền thông của công ty); Appointment (Bổ nhiệm); Financial (Tài chính); Regulatory (Cơ quan quản lí, chính sách); Sales (Bán hàng); M&A (Merge & Acquisition): Sáp nhập; Legal (Luật, tính hợp pháp); Dividend Policy (Chính sách cổ tức); Risks (rủi ro - ví dụ operation risk, credit risk - rủi ro tín dụng, reputation risk); Rumors (tin đồn); Strategy (chiến lược); Options (quyền chọn); IPO (initial public offering): lên sàn, niêm yết; Signal (tín hiệu để mua bán cổ phiếu); Coverage (báo cáo khuyến nghị buy sell hold của analysts); Fundamentals (các chỉ số trong phân tích cơ bản như P/E, P/B, Liabilites to Asset ratio); Insider Activity (các hoạt động nội bộ của công ty); Price Action (biến động giá); Buyside (các quĩ đầu tư, công ty nhỏ) ngược với sellside IB (Investment Banks); Technical Analysis (Phân tích kĩ thuật); Trade (thương mại, xuất nhập khẩu); Central Banks (Ngân hàng Trung ương, ở VN: Ngân hàng nhà nước, SBV); Currency (tiền tệ, tỉ giá); Conditions (điều kiện); Market (thị trường); Volatility (độ biến động, rủi ro); Investor Sentiment (Tâm lý chung của nhà đầu tư) lạc quan, lo lắng, chờ đợi...; Retail Investor Behavior (Hành vi của nhà đầu tư cá nhân) FOMO, hoảng loạn, giữ tiền mặt…; Speculation (Đầu cơ, hành vi đầu tư theo tin đồn hoặc kỳ vọng ngắn hạn); Domestic Institutional Behavior (Hành vi của tổ chức trong nước: tự doanh, bảo hiểm, quỹ trong nước) mua ròng, bán ròng, giảm tỷ trọng, rút khỏi cổ phiếu, các giao dịch thỏa thuận lớn giữa các tổ chức nội bộ; Foreign Institutional Behavior (Hành vi của nhà đầu tư tổ chức nước ngoài: ETF, quỹ ngoại, nhà đầu tư nước ngoài) mua ròng, bán ròng, tin tức đưa cổ phiếu vào, ra danh mục ETF, cảnh báo rủi ro, hạ mức xếp hạng cổ phiếu từ các tổ chức nước ngoài; Black Swan Event (Sự kiện thiên nga đen: hiếm gặp, khó dự đoán, gây ảnh hưởng nghiêm trọng như khủng hoảng, chiến tranh, dịch bệnh...).
2. Ảnh hưởng nội dung đến các khía cạnh tương ứng. Với mỗi chỉ số ảnh hưởng nên là số thực trong khoảng từ -1 (thật sự tiêu cực) đến 1 (thật sự tích cực)
3. Đảm bảo rằng các khía cạnh mà bạn trích xuất liên quan đến vấn đề của đoạn bài báo thời sự. Và khía cạnh nào bạn phân vân hãy xem không ảnh hưởng thì đánh là 0.
4. Chú ý là dựa vào ảnh hưởng của nội dung đến các khía cạnh. Khi cho tôi kết quả hãy theo format: có kí tự '#' trước khía cạnh, phía sau khía cạnh là con số ảnh hưởng nội dung, ví dụ về format '#khía cạnh1 1#khía cạnh2 -1#khía cạnh3 0'. Tuân thủ theo format của tôi, không làm khác.'''
    print(init_system_prompt)

    init_messages = [
      {"role": "system", "content": init_system_prompt},
      {"role": "user", "content": init_user_prompt},
      {"role": "assistant", "content": init_assistant},
    ]
    try:
      score_sentiment(original_file, destination_file, init_messages)
    except Exception as e:
      print(f"Lỗi khi xử lý cổ phiếu {ticker}: {e}")
      continue

    print("Đã xử lý xong cho cổ phiếu "+str(ticker))

In [ ]:
tickers = ['ACB', 'BCM', 'BID','BVH','CTG','FPT','GAS','GVR','HDB','HPG','LPB','MBB','MSN','MWG','PLX','SAB','SHB','SSB','SSI','STB','TCB','TPB','VCB','VHM','VIB','VIC','VJC','VNM','VPB','VRE']

score_sentiment_for_vn30(tickers)

Đang xử lý cho cổ phiếu FPT
Bạn là trợ lý hữu ích giúp tạo các cặp 'khía cạnh' - 'cảm xúc' từ một 'đoạn bài báo thời sự' cho cổ phiếu FPT. Dưới đây là các yêu cầu khi trích xuất khía cạnh và cảm xúc:
1. Các khía cạnh được trích xuất bao gồm: Reputation (Danh tiếng của công ty); Company Communication (Truyền thông của công ty); Appointment (Bổ nhiệm); Financial (Tài chính); Regulatory (Cơ quan quản lí, chính sách); Sales (Bán hàng); M&A (Merge & Acquisition): Sáp nhập; Legal (Luật, tính hợp pháp); Dividend Policy (Chính sách cổ tức); Risks (rủi ro - ví dụ operation risk, credit risk - rủi ro tín dụng, reputation risk); Rumors (tin đồn); Strategy (chiến lược); Options (quyền chọn); IPO (initial public offering): lên sàn, niêm yết; Signal (tín hiệu để mua bán cổ phiếu); Coverage (báo cáo khuyến nghị buy sell hold của analysts); Fundamentals (các chỉ số trong phân tích cơ bản như P/E, P/B, Liabilites to Asset ratio); Insider Activity (các hoạt động nội bộ của công ty); Price Action (biến đ

Phân tích tin tức:   0%|          | 0/346 [00:00<?, ?it/s]


📝 Đang chấm điểm xúc cảm cho bài báo thứ 1/346: Tiêu đề: Cổ phiếu FPT lập đỉnh giá mới
response ChatCompletion(id='chatcmpl-Bc9BewatzlCy62HeuPFZIvjW4pfj6', choices=[Choice(finish_reason='stop', index=0, logprobs=None, message=ChatCompletionMessage(content='#Reputation 0.0#Company Communication 0.0#Appointment 0.0#Financial 0.5#Regulatory 0.0#Sales 0.0#M&A 0.0#Legal 0.0#Dividend Policy 0.0#Risks 0.0#Rumors 0.0#Strategy 0.0#Options 0.0#IPO 0.0#Signal 0.7#Coverage 0.5#Fundamentals 0.6#Insider Activity 0.0#Price Action 0.8#Buyside 0.0#Technical Analysis 0.6#Trade 0.0#Central Banks 0.0#Currency 0.0#Conditions 0.0#Market 0.4#Volatility 0.3#Investor Sentiment 0.5#Retail Investor Behavior 0.0#Speculation 0.0#Domestic Institutional Behavior 0.0#Foreign Institutional Behavior 0.3#Black Swan Event 0.0', role='assistant', function_call=None, tool_calls=None, refusal=None, annotations=[]))], created=1748431478, model='gpt-4o-2024-08-06', object='chat.completion', service_tier='default', system_fin

Phân tích tin tức:   0%|          | 0/305 [00:00<?, ?it/s]


📝 Đang chấm điểm xúc cảm cho bài báo thứ 1/305: Tiêu đề: Ông Nguyễn Đức Tài chỉ mua 11% lượng cổ phiếu MWG đăng ký
response ChatCompletion(id='chatcmpl-Bc9wsTYjn02cUTmn7E8XhAsCTx5Ar', choices=[Choice(finish_reason='stop', index=0, logprobs=None, message=ChatCompletionMessage(content='#Reputation -0.4#Company Communication 0.0#Appointment 0.0#Financial -0.5#Regulatory 0.0#Sales -0.3#M&A 0.0#Legal 0.0#Dividend Policy 0.0#Risks -0.6#Rumors 0.0#Strategy -0.3#Options 0.0#IPO 0.0#Signal -0.4#Coverage 0.0#Fundamentals -0.4#Insider Activity 0.2#Price Action -0.5#Buyside 0.0#Technical Analysis 0.0#Trade 0.0#Central Banks 0.0#Currency 0.0#Conditions -0.5#Market -0.4#Volatility -0.5#Investor Sentiment -0.6#Retail Investor Behavior -0.4#Speculation 0.0#Domestic Institutional Behavior 0.0#Foreign Institutional Behavior -0.6#Black Swan Event 0.0', role='assistant', function_call=None, tool_calls=None, refusal=None, annotations=[]))], created=1748434406, model='gpt-4o-2024-08-06', object='chat.compl

...


📝 Đang chấm điểm xúc cảm cho bài báo thứ 1/200: Tiêu đề: Các tỷ phú giàu nhất Việt Nam 2024: Nhiều tỷ phú mới lộ diện top 10, ông Phạm Nhật Vượng vững ngôi 15 năm
response ChatCompletion(id='chatcmpl-BcD0GkrL6GHyqZTJNa2LMhbBnShcx', choices=[Choice(finish_reason='stop', index=0, logprobs=None, message=ChatCompletionMessage(content='#Reputation 0.2#Company Communication 0.0#Appointment 0.0#Financial 0.3#Regulatory 0.0#Sales 0.0#M&A 0.0#Legal 0.0#Dividend Policy 0.0#Risks 0.0#Rumors 0.0#Strategy 0.1#Options 0.0#IPO 0.0#Signal 0.0#Coverage 0.0#Fundamentals 0.1#Insider Activity 0.0#Price Action 0.0#Buyside 0.0#Technical Analysis 0.0#Trade 0.0#Central Banks 0.0#Currency 0.0#Conditions 0.0#Market 0.1#Volatility 0.0#Investor Sentiment 0.2#Retail Investor Behavior 0.0#Speculation 0.0#Domestic Institutional Behavior 0.0#Foreign Institutional Behavior 0.0#Black Swan Event 0.0', role='assistant', function_call=None, tool_calls=None, refusal=None, annotations=[]))], created=1748446148, model='gpt-

Phân tích tin tức:   0%|          | 0/123 [00:00<?, ?it/s]


📝 Đang chấm điểm xúc cảm cho bài báo thứ 1/123: Tiêu đề: Tổng giám đốc VEAM bị khởi tố: Khối ngoại bán tháo, cổ phiếu giảm mạnh
response ChatCompletion(id='chatcmpl-BcDSEjWTmwSvxsxfD5H88i0gjN4Ro', choices=[Choice(finish_reason='stop', index=0, logprobs=None, message=ChatCompletionMessage(content='#Reputation -0.6#Company Communication 0.0#Appointment -0.5#Financial -0.4#Regulatory -0.3#Sales 0.0#M&A 0.0#Legal -0.7#Dividend Policy 0.0#Risks -0.6#Rumors 0.0#Strategy 0.0#Options 0.0#IPO 0.0#Signal -0.5#Coverage 0.0#Fundamentals -0.4#Insider Activity -0.5#Price Action -0.4#Buyside 0.0#Technical Analysis 0.0#Trade 0.0#Central Banks 0.0#Currency 0.0#Conditions -0.3#Market -0.4#Volatility -0.5#Investor Sentiment -0.6#Retail Investor Behavior 0.2#Speculation 0.0#Domestic Institutional Behavior 0.3#Foreign Institutional Behavior -0.7#Black Swan Event 0.0', role='assistant', function_call=None, tool_calls=None, refusal=None, annotations=[]))], created=1748447882, model='gpt-4o-2024-08-06', obje

Phân tích tin tức:   0%|          | 0/194 [00:00<?, ?it/s]


📝 Đang chấm điểm xúc cảm cho bài báo thứ 1/194: Tiêu đề: Các tỷ phú giàu nhất Việt Nam 2024: Nhiều tỷ phú mới lộ diện top 10, ông Phạm Nhật Vượng vững ngôi 15 năm
response ChatCompletion(id='chatcmpl-BcDi7VG8BXoqgfyGDX9KAHi31TN9B', choices=[Choice(finish_reason='stop', index=0, logprobs=None, message=ChatCompletionMessage(content='#Reputation 0.2#Company Communication 0.0#Appointment 0.0#Financial 0.3#Regulatory 0.0#Sales 0.0#M&A 0.2#Legal 0.0#Dividend Policy 0.0#Risks -0.2#Rumors 0.0#Strategy 0.1#Options 0.0#IPO 0.0#Signal 0.1#Coverage 0.0#Fundamentals 0.2#Insider Activity 0.0#Price Action 0.1#Buyside 0.0#Technical Analysis 0.0#Trade 0.0#Central Banks 0.0#Currency 0.0#Conditions 0.0#Market 0.2#Volatility 0.0#Investor Sentiment 0.3#Retail Investor Behavior 0.0#Speculation 0.0#Domestic Institutional Behavior 0.0#Foreign Institutional Behavior 0.0#Black Swan Event 0.0', role='assistant', function_call=None, tool_calls=None, refusal=None, annotations=[]))], created=1748448867, model='gpt